An example using Principal Component Analysis using Larch

In [1]:
from pathlib import Path
from larch.io import read_athena
from larch.xafs import pre_edge
from larch.math import pca_train, pca_fit

from larch.plot.plotly_xafsplots import plot_mu, plot_pca_components, plot_pca_weights, plot_pca_fit

filename = Path('..', 'pca', 'cyanobacteria.prj')
prj = read_athena(filename)

In [2]:
# show the groups in this project file
prj

<Group 0x18a584250>

In [3]:
# select the groups that are "Standards" and "Unknowns"
standards = (prj.Au_foil, prj.Au3_Cl_aq, prj.Au_hydroxide, prj.Au_thiocyanide,
             prj.Au_sulphide, prj.Au_thiosulphate_aq)

unknowns = (prj.d_0_12, prj.d_2_42, prj.d_4_73, prj.d_7_03,
           prj.d_9_33, prj.d_20, prj.d_33, prj.d_720)

# make sure pre_edge() is run with the same params for all groups
for grp in standards + unknowns:
    pre_edge(grp, pre1=-150, pre2=-30, nnorm=1, norm1=150, norm2=850)

In [4]:
# let's plot the Standards.  
# With plotly_xafsplots, we'll re-use the figure to draw multiple spectra
fig = None 
for g in standards:
    fig = plot_mu(g, show_norm=True, fig=fig, label=g.label, emin=11850, emax=12150, show=False)
fig.show(title='Au Standards', xlabel='Energy (eV)', ylabel='Normalized XAFS')

# the Standards look reasonably well normalized, so we can use them to train a model

In [5]:
# now we train model with standards
au_pcamodel = pca_train(standards, arrayname='norm', xmin=11870, xmax=12030)

In [6]:
au_pcamodel

<Group 0x18b6fadd0>

In [7]:
# print out the weights of the components
total = 0
print(" Comp #  |  Weight   |  Cumulative Total")
for i, weight in enumerate(au_pcamodel.variances):
    total = total + weight
    print("  %3i    | %8.5f  | %8.5f " % (i+1, weight, total))

 Comp #  |  Weight   |  Cumulative Total
    1    |  0.76698  |  0.76698 
    2    |  0.17138  |  0.93836 
    3    |  0.04203  |  0.98039 
    4    |  0.01884  |  0.99923 
    5    |  0.00077  |  1.00000 
    6    |  0.00000  |  1.00000 


In [8]:
# plot the components
plot_pca_components(au_pcamodel, min_weight=0.005)

In [9]:
# now make a SCREE plot of component weight and Indicator value
scree = plot_pca_weights(au_pcamodel, min_weight=0.005)

In [10]:
# with this model now trained, we can fit unknown data to model to see if that
# dataset can be described as a sum of those components.
pca_fit(prj.d_720, au_pcamodel, ncomps=4)

# show result
prj.d_720.pca_result

<Group 0x18b7a3410>

In [11]:
# plot this fit
plot_pca_fit(prj.d_720, with_components=True)

(<larch.plot.plotly_xafsplots.PlotlyFigure at 0x18b8f2f10>,
 <larch.plot.plotly_xafsplots.PlotlyFigure at 0x18b902b10>)